# Luxo Log Analysis

## Takeaways
* Voltage is very important. But 10s is too much voltage for the moteus! 8s should be ok.
* Important that the moteus ramps up torque quickly. Need high bandwidth etc.

In [139]:
import pickle
import numpy as np
import moteus
# import pandas as pd
import matplotlib.pyplot as plt
import plotly
import scipy.signal as signal
import scipy.integrate as integrate

In [140]:
import plotly.express as px
import plotly.graph_objects as go
import plotly.subplots as sp

In [141]:
def process_data(data, start_idx=None, end_idx=None):
    data_subset = data[start_idx:end_idx]
    torques = np.array([datum[1].values[moteus.Register.TORQUE] for datum in data_subset])
    ts = np.array([datum[0] for datum in data_subset])
    positions = np.array([datum[1].values[moteus.Register.POSITION] for datum in data_subset])
    velocities = np.array([datum[1].values[moteus.Register.VELOCITY] for datum in data_subset])
    accel = np.concatenate(([0], np.diff(velocities))) / np.mean(np.diff(ts))
    sos = signal.butter(2, 0.25, output='sos')
    accel_filt = signal.sosfiltfilt(sos, accel)
    print("dt: ", np.mean(np.diff(ts)))
    powers = torques * velocities * 2 * np.pi # Convert to W
    energy = integrate.cumulative_trapezoid(y=powers, x=ts) # J
    return {"ts":ts, 
            "positions":positions, 
            "velocities":velocities, 
            "accels":accel_filt, 
            "torques":torques, 
            "powers":powers,
            "energy":energy}

In [142]:
def plot_data(data_dict):
    fig = sp.make_subplots(rows=len(data_dict), cols=1, shared_xaxes=True, vertical_spacing = 0.01)
    fig_combined = go.Figure()
    x = data_dict["ts"]
    for i, (key, data) in enumerate(data_dict.items()):
        if key == "ts":
            continue
        fig.add_trace(go.Scatter(name=key, x=x, y=data), row=i, col=1)
        fig_combined.add_trace(go.Scatter(name=key, x=x, y=data/np.max(data)))
    fig.update_layout(height=100*len(data_dict), width=800)
    fig.show()
    fig_combined.update_layout(height=100*len(data_dict), width=800)
    fig_combined.show()

def compare_data(data1, data2):
    fig = sp.make_subplots(rows=3, cols=1, shared_xaxes=True, vertical_spacing = 0.01)
    fig.add_trace(go.Scatter(name='torque_1', x=data1["ts"], y=data1["torques"]), row=1, col=1)
    fig.add_trace(go.Scatter(name='torque_2', x=data2["ts"], y=data2["torques"]), row=1, col=1)
    fig.add_trace(go.Scatter(name='vel_1', x=data1["ts"], y=data1["velocities"]), row=2, col=1)
    fig.add_trace(go.Scatter(name='vel_2', x=data2["ts"], y=data2["velocities"]), row=2, col=1)
    fig.add_trace(go.Scatter(name='pos_1', x=data1["ts"], y=data1["positions"]), row=3, col=1)
    fig.add_trace(go.Scatter(name='pos_2', x=data2["ts"], y=data2["positions"]), row=3, col=1)
    fig.update_layout(height=600, width=800)
    fig.show()

In [143]:
from IPython.display import display, HTML
display(HTML("<style>div.output_scroll { height: 44em; }</style>"))

# Torque PD No Load

In [144]:
data_noload = pickle.load(open("logs/log_1_24_22_unloaded.pickle","rb+"))
data_noload = process_data(data_noload)#, 200, 300)
plot_data(data_noload)

dt:  0.00233734813645656


# Torque PD Jump

In [145]:
data = pickle.load(open("logs/log_1_22_22_torquepd_jump.pickle","rb+"))
data_jump1 = process_data(data)#, 200, 300)
plot_data(data_jump1)

dt:  0.0023883000519830237


# Torque PD Jump - No Head

In [146]:
data = pickle.load(open("logs/log_1_22_22_torquepd_jump_nohead.pickle","rb+"))
data_nohead = process_data(data)#, 200, 300)
plot_data(data_nohead)

dt:  0.0023219926675468166


# TorquePD Jump - no head, with attached base

In [147]:
data = pickle.load(open("logs/log_1_24_22_jump_base_2_more_vert.pickle","rb+"))
data_base = process_data(data)#, 200, 300)
plot_data(data_base)

dt:  0.002231187979971166


# Compare noload to jump with head

In [148]:
compare_data(data_noload, data_jump1)

# TorquePD Jump - With 5s battery attached

In [149]:
data_batt_jump_4 = pickle.load(open("logs/log_1_25_22_batt_jump_4.pickle","rb+"))
data_batt_jump_4 = process_data(data_batt_jump_4)#, 200, 300)
plot_data(data_batt_jump_4)

dt:  0.002654918245395551


# Jump w/head -- VS -- jump w/ battery
Very similar trajectories

In [150]:
compare_data(data_jump1, data_batt_jump_4)

# Jump w/o head  -- VS -- jump w/ head - battery
Very similar motor trajectories but a little more delay when loaded with battery

In [151]:
compare_data(data_nohead, data_batt_jump_4)

# Unloaded 10s
Peak vel of 92rps

In [152]:
data_10s_noload = pickle.load(open("logs/log_1_27_22_10s_unloaded.pickle","rb+"))
data_10s_noload = process_data(data_10s_noload)#, 200, 300)
plot_data(data_10s_noload)

dt:  0.0024951889307172465


# 8S no load -- VS -- 10s no load
68rps vs 92rps peak velocity. More overshoot with 10s.

In [153]:
compare_data(data_noload, data_10s_noload)

# Jump 10s


In [154]:
data_10s_jump = pickle.load(open("logs/log_1_27_22_jump1.pickle","rb+"))
data_10s_jump = process_data(data_10s_jump)
plot_data(data_10s_jump)

dt:  0.002776011895905271
